In [1]:
using LinearAlgebra
using TensorOperations

In [2]:

function transform_tensor(A::Array, T::AbstractMatrix)
    n = ndims(A)
    A_new = A

    for idx in 1:n
        # Permute so that idx becomes the first axis
        perm = [idx; setdiff(1:n, idx)]
        A_perm = permutedims(A_new, perm)

        # Flatten all other dimensions
        sz = size(A_perm)
        A_mat = reshape(A_perm, sz[1], :)

        # Contract with transformation matrix on the first index
        A_mat_new = T * A_mat

        # Reshape back
        new_dims = (size(T, 1), sz[2:end]...)
        A_perm_new = reshape(A_mat_new, new_dims)

        # Inverse permutation to restore original order
        invp = invperm(perm)
        A_new = permutedims(A_perm_new, invp)
    end

    return A_new
end

transform_tensor (generic function with 1 method)

This is a tranformation matrix used for $D_{3d}$ symmetry with $C_3$ along (1,1,1) in cubic coordinates. The standard $D_{3d}$ coordinates
have $z\parallel C_3$ (1,1,1) and $x\parallel C'_2$ (1,0,-1). 

In [4]:
T = [1/sqrt(2) 0 -1/sqrt(2); -1/sqrt(6) 2/sqrt(6) -1/sqrt(6); 1/sqrt(3) 1/sqrt(3) 1/sqrt(3)]'

3×3 adjoint(::Matrix{Float64}) with eltype Float64:
  0.707107  -0.408248  0.57735
  0.0        0.816497  0.57735
 -0.707107  -0.408248  0.57735

In [5]:
T'*T

3×3 Matrix{Float64}:
 1.0  0.0  0.0
 0.0  1.0  0.0
 0.0  0.0  1.0

This is the $x\cdot z\otimes R_z-y\cdot z\otimes R_x$ tensor:

In [7]:
F=zeros(3,3,3);
F[1,3,2]=1;
F[3,1,2]=1;
F[2,3,1]=-1;
F[3,2,1]=-1;

In [8]:
F_new=transform_tensor(F,T)

3×3×3 Array{Float64, 3}:
[:, :, 1] =
  0.0       -0.333333  0.333333
 -0.333333  -0.666667  0.0
  0.333333   0.0       0.666667

[:, :, 2] =
 0.666667   0.333333   0.0
 0.333333   0.0       -0.333333
 0.0       -0.333333  -0.666667

[:, :, 3] =
 -0.666667  0.0       -0.333333
  0.0       0.666667   0.333333
 -0.333333  0.333333   0.0

In [9]:
k_in = [0 ,0, 1]
k_out = rand(3)
@tensor F[i,j,k]*k_out[i]*k_out[j]*k_in[k]

0.0

In [10]:
k_in = [1 ,1, 1]
k_out = rand(3)
@tensor F_new[i,j,k]*k_out[i]*k_out[j]*k_in[k]

-2.42861286636753e-17

This is the $(x^2-y^2)\otimes R_x-x\cdot y\otimes R_y$ tensor:

In [12]:
F2=zeros(3,3,3)
F2[1,1,1]=-1
F2[2,2,1]=1
F2[1,2,2]=1
F2[2,1,2]=1
F2_new=transform_tensor(F2,T)

3×3×3 Array{Float64, 3}:
[:, :, 1] =
  1.94289e-16  -0.471405   0.471405
 -0.471405      0.471405   0.0
  0.471405      0.0       -0.471405

[:, :, 2] =
 -0.471405   0.471405   0.0
  0.471405   0.0       -0.471405
  0.0       -0.471405   0.471405

[:, :, 3] =
  0.471405   0.0       -0.471405
  0.0       -0.471405   0.471405
 -0.471405   0.471405  -1.94289e-16

In [13]:
k_in = [1 ,1, 1]
k_out = rand(3)
@tensor F2_new[i,j,k]*k_out[i]*k_out[j]*k_in[k]

1.3660947373317356e-17